## The CIFAR10 Dataset

[Keras CIFAR10 info page](https://keras.io/api/datasets/cifar10)
&nbsp;&nbsp;&nbsp;&nbsp;&nbsp;&nbsp;&nbsp;&nbsp;&nbsp;&nbsp;
[CIFAR10 home page](https://www.cs.toronto.edu/~kriz/cifar.html)

### Preliminaries

In [ ]:
import random
import numpy as np
import matplotlib.pyplot as plt
plt.rcParams["figure.figsize"] = (2,2)  # default figure size: 2x2 inches

In [ ]:
# generalized version of plot_history that plots validation data if available

def plot_history(history):
    loss_values = history.history['loss']
    accuracy_values = history.history['accuracy']
    validation = 'val_loss' in history.history
    if validation:
        val_loss_values = history.history['val_loss']
        val_accuracy_values = history.history['val_accuracy']
    epoch_nums = range(1, len(loss_values)+1)
    plt.figure(figsize=(12,4)) # width, height in inches
    plt.subplot(1, 2, 1)
    if validation:
        plt.plot(epoch_nums, loss_values, 'r', label="Training loss")
        plt.plot(epoch_nums, val_loss_values, 'r--', label="Validation loss")
        plt.title("Training/validation loss")
        plt.legend()
    else:
        plt.plot(epoch_nums, loss_values, 'r', label="Training loss")
        plt.title("Training loss")
    plt.xlabel("Epochs")
    plt.ylabel("Loss")
    plt.subplot(1, 2, 2)
    if validation:
        plt.plot(epoch_nums, accuracy_values, 'b', label='Training accuracy')
        plt.plot(epoch_nums, val_accuracy_values, 'b--', label='Validation accuracy')
        plt.title("Training/validation accuracy")
        plt.legend()
    else:
        plt.plot(epoch_nums, accuracy_values, 'b', label='Training accuracy')
        plt.title("Training accuracy")
    plt.xlabel("Epochs")
    plt.ylabel("Accuracy")
    plt.ylim(0, 1)
    plt.show()
    
from tensorflow.keras.models import Model

# this version of show_channels does not call preprocess_image

def show_channels(network, image, layer_name, channels=range(20), cmap='gray', cols=5):
    # channels can be a number like 0 or a sequence like [0, 2, 4] or range(10)
    layer_names = [layer.name for layer in network.layers]
    if layer_name not in layer_names:
        print(f'No such layer: {layer_name}')
        return
    # generate activation maps for layer_name
    input_tensor = network.layers[0].input
    output_tensor = network.get_layer(layer_name).output
    activation_model = Model(inputs=input_tensor, outputs=output_tensor)
    batch = np.array([image])
    #output = activation_model.predict(batch)[0] # using predict causes a weird warning message
    output = activation_model(batch)[0].numpy()
    h, w, d = output.shape
    # display activation maps
    if type(channels) is int:
        channels  = [channels]
    rows = len(channels) // cols
    if len(channels) > rows*cols:
        rows += 1
    plt.figure(figsize=(3*cols,3*rows))  # (width, height) in inches
    k = 0
    for channel in channels:
        if 0 <= channel < d:
            k += 1
            plt.subplot(rows, cols, k)
            plt.imshow(output[:,:,channel], cmap=cmap)
            plt.title(f'channel {channel}')
            plt.axis('off')

### CIFAR10 categories

*   0 = airplane
*   1 = car
*   2 = bird
*   3 = cat
*   4 = deer
*   5 = dog
*   6 = frog
*   7 = horse
*   8 = ship
*   9 = truck

### Load and examine the data

In [ ]:
from tensorflow.keras.datasets import cifar10

In [ ]:
(train_images,train_labels), (test_images,test_labels) = cifar10.load_data()

In [ ]:
train_images.shape

In [ ]:
train_images.dtype, train_images.min(), train_images.max()

In [ ]:
train_images[0]

In [ ]:
plt.imshow(train_images[0]);

In [ ]:
train_labels.shape

In [ ]:
train_labels[0]

In [ ]:
train_labels[:10]

In [ ]:
train_labels[0][0]

In [ ]:
train_labels = train_labels.reshape(50000)

In [ ]:
train_labels.shape

In [ ]:
train_labels[0]

In [ ]:
train_labels[:10]

In [ ]:
test_labels = test_labels.reshape(len(test_labels))

In [ ]:
test_labels.shape

In [ ]:
names = 'airplane car bird cat deer dog frog horse ship truck'.split()

In [ ]:
names

In [ ]:
names[6]

In [ ]:
def show_random_image():
    n = random.randrange(len(train_images))
    category_num = train_labels[n]
    category_name = names[category_num]
    print(f"train_images[{n}]: {category_name}")
    plt.imshow(train_images[n])

In [ ]:
show_random_image()

In [ ]:
# show_random_selection() shows training images from all categories
# show_random_selection(n) shows training images from category n

def show_random_selection(category_num=None):
    if category_num == None:
        which = range(len(train_images))
    elif 0 <= category_num < len(names):
        which = [i for i in range(len(train_images)) if train_labels[i] == category_num]
    else:
        print("category out of range")
        return
    plt.figure(figsize=(15,15))  # (width, height) in inches
    rows, columns = 5, 6
    for k in range(1, columns*rows+1):
        i = random.choice(which)
        plt.subplot(rows, columns, k)
        category_num = train_labels[i]
        plt.title(names[category_num])
        plt.axis('off')
        plt.imshow(train_images[i])

In [ ]:
show_random_selection(9)

In [ ]:
from tensorflow.keras.utils import to_categorical

In [ ]:
# create the one-hot target vectors
train_targets = to_categorical(train_labels, num_classes=10)
test_targets = to_categorical(test_labels, num_classes=10)

In [ ]:
test_targets[99]

In [ ]:
test_labels[99]

In [ ]:
names[7]

In [ ]:
plt.imshow(test_images[99]);

### Optional: Convert images to grayscale

In [ ]:
frog = train_images[0]

In [ ]:
frog.shape

In [ ]:
plt.imshow(frog);

Let's start with just the top row of pixels in the image:

In [ ]:
top_row = frog[0]  # top row of pixels

In [ ]:
top_row

In [ ]:
len(top_row)

We can average together the three RGB values for each pixel like this:

In [ ]:
np.dot(top_row, [1/3, 1/3, 1/3])

In [ ]:
len(np.dot(top_row, [1/3, 1/3, 1/3]))

In [ ]:
np.round(np.dot(top_row, [1/3, 1/3, 1/3]))

In [ ]:
np.round(np.dot(top_row, [1/3, 1/3, 1/3])).astype('uint8')

We can also apply the operation to the whole image:

In [ ]:
np.round(np.dot(frog, [1/3, 1/3, 1/3])).astype('uint8')

In [ ]:
# convert a color image to grayscale

def color2gray(image):
    assert image.dtype == 'uint8', "image must be of type uint8"
    rgb_weights = [1/3, 1/3, 1/3]
    gray = np.round(np.dot(image, rgb_weights)).astype('uint8')
    return gray

In [ ]:
frog_gray = color2gray(frog)

In [ ]:
frog_gray.shape

In [ ]:
plt.imshow(frog_gray);  # default colormap

In [ ]:
plt.imshow(frog_gray, cmap='gray');

In [ ]:
# version 2:
# - corrects for perceptual effects
# - returns shape (height, width, 1)

def color2gray(image):
    assert image.dtype == 'uint8', "image must be of type uint8"
    rgb_weights = [0.299, 0.587, 0.114]  # corrects for perceptual effects
    gray = np.round(np.dot(image, rgb_weights)).astype('uint8')
    gray = gray.reshape(gray.shape + (1,))  # reshape as (height, width, 1)
    return gray

In [ ]:
plt.imshow(color2gray(frog), cmap='gray');

In [ ]:
color2gray(train_images[0]).shape

We can convert all training images at once to grayscale:

In [ ]:
color2gray(train_images).shape

In [ ]:
train_images_gray = color2gray(train_images)
test_images_gray = color2gray(test_images)

In [ ]:
test_images_gray.shape

In [ ]:
test_images_gray.dtype

In [ ]:
plt.imshow(test_images_gray[99], cmap='gray');

### Prepare the training data

In [ ]:
(train_images,train_labels), (test_images,test_labels) = cifar10.load_data()
# simplify the labels
train_labels = train_labels.reshape(len(train_labels))
test_labels = test_labels.reshape(len(test_labels))

In [ ]:
train_images.dtype, train_images.min(), train_images.max()

In [ ]:
train_images.shape

In [ ]:
test_images.shape

In [ ]:
def normalize(image):
    assert image.dtype == 'uint8', "image must be of type uint8"
    return (image / 255).astype('float32')

In [ ]:
normalize(train_images[0])

In [ ]:
train_images = normalize(train_images)
test_images = normalize(test_images)

In [ ]:
train_images.dtype, train_images.min(), train_images.max()

In [ ]:
plt.imshow(train_images[0]);

### Build a convolutional neural network

In [ ]:
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense, Flatten
from tensorflow.keras.layers import Conv2D, MaxPooling2D

In [ ]:
def build_convnet():
    convnet = Sequential()
    convnet.add(Conv2D(64, (3,3), activation='relu', name='conv1', input_shape=(32,32,3)))
    convnet.add(MaxPooling2D((2,2), name='pool1'))
    convnet.add(Conv2D(64, (3,3), activation='relu', name='conv2'))
    convnet.add(MaxPooling2D((2,2), name='pool2'))
    convnet.add(Conv2D(64, (3,3), activation='relu', name='conv3'))
    convnet.add(Flatten())
    convnet.add(Dense(64, activation='relu', name='hidden'))
    convnet.add(Dense(10, activation='softmax', name='output'))
    
    convnet.compile(loss='categorical_crossentropy',
                    optimizer='rmsprop',
                    metrics=['accuracy'])
    return convnet

In [ ]:
convnet = build_convnet()

In [ ]:
convnet.summary()

In [ ]:
history = convnet.fit(train_images, train_targets, epochs=10, batch_size=64)

In [ ]:
convnet.evaluate(train_images, train_targets)

In [ ]:
convnet.evaluate(test_images, test_targets)

In [ ]:
plot_history(history)

In [ ]:
outputs = convnet.predict(test_images)

In [ ]:
outputs.shape

In [ ]:
predictions = [np.argmax(output) for output in outputs]

In [ ]:
wrong = [i for i in range(len(predictions)) if predictions[i] != test_labels[i]]

In [ ]:
print(f"Misclassified {len(wrong)} test images out of {len(test_images)}")

In [ ]:
def show_wrong_images(network):
    outputs = network.predict(test_images)
    predictions = [np.argmax(output) for output in outputs]
    wrong = [i for i in range(len(predictions)) if predictions[i] != test_labels[i]]
    print(f"Misclassified {len(wrong)} test images out of {len(test_images)}")
    plt.figure(figsize=(12,12))  # (width, height) in inches
    rows, columns = 5, 6
    for i in range(1, columns*rows+1):
        w = random.choice(wrong)
        img = test_images[w]
        predicted_name = names[predictions[w]]
        correct_name = names[test_labels[w]]
        plt.subplot(rows, columns, i)
        plt.title(f'"{predicted_name}"  ({correct_name})')
        plt.axis('off')
        plt.imshow(img)  #, cmap='gray')

A random sampling of misclassified images:

In [ ]:
show_wrong_images(convnet)

### Use a validation set

In [ ]:
train_images.shape

In [ ]:
train_labels.shape

In [ ]:
train_targets.shape

In [ ]:
# of images to use for validation set
split = 10000

val_images = train_images[:split]
val_targets = train_targets[:split]
val_labels = train_labels[:split]

subset_images = train_images[split:]
subset_targets = train_targets[split:]
subset_labels = train_labels[split:]

print(f"Using {len(subset_images)} images for training, {len(val_images)} for validation")

In [ ]:
subset_images.shape

In [ ]:
convnet = build_convnet()

In [ ]:
history = convnet.fit(subset_images, subset_targets,
                      validation_data=(val_images, val_targets),
                      epochs=10, batch_size=64)

In [ ]:
convnet.evaluate(subset_images, subset_targets)

In [ ]:
convnet.evaluate(test_images, test_targets)

In [ ]:
plot_history(history)

In [ ]:
convnet = build_convnet()

In [ ]:
history = convnet.fit(train_images, train_targets, epochs=4, batch_size=64)

In [ ]:
convnet.evaluate(train_images, train_targets)

In [ ]:
convnet.evaluate(test_images, test_targets)

### Cats vs. Dogs

In [ ]:
def load_cifar10_subset(selected_classes=[]):
    if len(selected_classes) == 0:
        selected_classes = list(range(10))
    for n in selected_classes:
        assert type(n) == int and 0 <= n <= 9, "classes must be ints in range 0-9"
    # load the data
    (train_images,train_labels), (test_images,test_labels) = cifar10.load_data()
    # simplify the labels
    train_labels = train_labels.reshape(len(train_labels))
    test_labels = test_labels.reshape(len(test_labels))
    # extract the desired classes
    indices = [i for i in range(len(train_labels)) if train_labels[i] in selected_classes]
    selected_train_images = train_images[indices]
    selected_train_labels = train_labels[indices]
    indices = [i for i in range(len(test_labels)) if test_labels[i] in selected_classes]
    selected_test_images = test_images[indices]
    selected_test_labels = test_labels[indices]
    new_train_labels = np.array([selected_classes.index(i) for i in selected_train_labels])
    new_test_labels = np.array([selected_classes.index(i) for i in selected_test_labels])
    class_names = 'airplane car bird cat deer dog frog horse ship truck'.split()
    new_names = [class_names[n] for n in selected_classes]
    # normalize the images
    selected_train_images = normalize(selected_train_images)
    selected_test_images = normalize(selected_test_images)
    return ((selected_train_images,new_train_labels),
            (selected_test_images,new_test_labels),
            new_names)

In [ ]:
(train_images,train_labels), (test_images,test_labels), names = load_cifar10_subset([3,5])

In [ ]:
train_labels[:20]

In [ ]:
names

In [ ]:
plt.imshow(train_images[5]);

In [ ]:
plt.imshow(train_images[4]);

In [ ]:
# create the one-hot target vectors
train_targets = to_categorical(train_labels, num_classes=2)
test_targets = to_categorical(test_labels, num_classes=2)

In [ ]:
train_targets[0]

In [ ]:
show_random_selection(0)

In [ ]:
show_random_selection(1)

#### How well can you train the network to distinguish cats from dogs?

Try it!

### Dogs vs. Airplanes

In [ ]:
(train_images,train_labels), (test_images,test_labels), names = load_cifar10_subset([5,0])

# create the one-hot target vectors
train_targets = to_categorical(train_labels, num_classes=2)
test_targets = to_categorical(test_labels, num_classes=2)

In [ ]:
names

In [ ]:
show_random_selection()

#### How well can you train the network to distinguish dogs from airplanes?

Try it!

### Cars vs. Trucks vs. Ships vs. Airplanes

In [ ]:
(train_images,train_labels), (test_images,test_labels), names = load_cifar10_subset([1,9,8,0])

# create the one-hot target vectors
train_targets = to_categorical(train_labels, num_classes=4)
test_targets = to_categorical(test_labels, num_classes=4)

In [ ]:
show_random_selection()

Try it!

### Or some other combination of categories...